In [1]:
import csv
from enum import Enum
import cv2
import numpy as np
from time import time
import sys
sys.path.insert(0, "/home/adity/Desktop/projects/image_search/code/classifiers")

In [2]:
class YType(Enum):
    SAME = 0
    DIFFERENT = 1
    NONE = 2

class TestDataStructure:
    clientA = ''
    clientB = ''
    expected_y = YType.NONE
    predicted_y = YType.NONE

In [3]:
class Evaluation:
    def __init__(self, model=None, enable_accuracy=False, enable_auc=False, enable_confusion_matrix=False, enable_precision=False, enable_recall=False):
        self.model = model
        self.enable_accuracy = enable_accuracy
        self.enable_auc = enable_auc
        self.enable_confusion_matrix = enable_confusion_matrix
        self.enable_precision = enable_precision
        self.enable_recall = enable_recall
        self.dataset_path = "/home/adity/Desktop/projects/image_search/datasets/Test Data/"
        # no f1
        
    def prepare_test_Data(self, csv_file):
        list_A = []
        list_B = []
        line_number = 0
        with open(csv_file, 'r') as file:
            reader = csv.reader(file)
            for row in reader:
                if line_number == 0:
                    line_number += 1
                else:
                    if row[0] == '':
                        print()
                        list_A.append(None)
                    else:
                        list_A.append(row[0])
                    
                    if row[1] == '':
                        list_B.append(None)
                    else:
                        list_B.append(row[1])
                    line_number += 1
        print("Processed lines", {line_number})
        return list_A, list_B
    
    def prepare_test_data_Structure(self, list_A, list_B):
        test_data_list = []
        i = 0
        for item_A in list_A:
            j = 0
            for item_B in list_B:
                test_data = TestDataStructure()
                test_data.clientA = list_A[i]
                test_data.clientB = list_B[j]
                if i == j:
                    if list_A[i] and list_B[j]:
                        test_data.expected_y = YType.SAME
                    test_data_list.append(test_data)
                else:
                    if list_A[i] and list_B[j]:
                        test_data.expected_y = YType.DIFFERENT
                        test_data_list.append(test_data)
                j += 1
            i += 1
        return test_data_list
    
    def generate_output_lists(self, test_data_list):
        y_true = []
        y_pred = []
        i = 0
        for test_data in test_data_list:
            y_true.append(test_data.expected_y.value)
            y_pred.append(test_data.predicted_y.value)
            i += 1
        return y_true, y_pred
    
    def get_results_for_all_image_pairs(self, test_data_list, model):
        for test_data in test_data_list:
            if test_data.clientA != None and test_data.clientB != None:
                image_1 = cv2.imread(self.dataset_path + "Client1/" + test_data.clientA)
                image_2 = cv2.imread(self.dataset_path + "Client2/" + test_data.clientB)
                if type(image_1) == np.ndarray and type(image_2) == np.ndarray:
                    image_1 = cv2.resize(image_1, (250,250))
                    image_2 = cv2.resize(image_2, (250,250))
                    tic = time()
                    test_data.predicted_y = model.compare_image(image_1, image_2)
                    toc = time()
#                     print(test_data.clientA, test_data.clientB, ", Expected Y:" + str(test_data.expected_y), ", Predicted y:", str(test_data.predicted_y), "time taken:", toc - tic)

    def get_results_for_all_image_pairs_color(self, test_data_list, model):
        for test_data in test_data_list:
            if test_data.clientA != None and test_data.clientB != None:
                image_1 = cv2.imread(self.dataset_path + "Client1/" + test_data.clientA)
                image_2 = cv2.imread(self.dataset_path + "Client2/" + test_data.clientB)
                if type(image_1) == np.ndarray and type(image_2) == np.ndarray:
                    image_1 = cv2.resize(image_1, (250,250))
                    image_2 = cv2.resize(image_2, (250,250))
                    tic = time()
                    test_data.predicted_y = model.compare_image(image_1, image_2)
                    toc = time()
                    print(test_data.clientA, test_data.clientB, ", Expected Y:" + str(test_data.expected_y), ", Predicted y:", str(test_data.predicted_y), "time taken:", toc - tic)


In [4]:
eval_model = Evaluation()

In [5]:
list_A, list_B = eval_model.prepare_test_Data("/home/adity/Desktop/projects/image_search/datasets/Test Data/match.csv")
test_data = eval_model.prepare_test_data_Structure(list_A, list_B)
print(test_data[1].clientA, test_data[1].clientB, test_data[1].expected_y, test_data[1].predicted_y)
print(len(test_data))

Processed lines {496}
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Juicy Green Apple Shampoo  350ml'].jpg YType.DIFFERENT YType.NONE
164009


In [6]:
print(test_data[1].clientA, test_data[1].clientB, test_data[1].expected_y, test_data[1].predicted_y)

['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Juicy Green Apple Shampoo  350ml'].jpg YType.DIFFERENT YType.NONE


In [7]:
import sys
sys.path.insert(0, "/home/adity/Desktop/projects/image_search/code/classifiers")

In [8]:
from template_matching import TemplateMatching

In [9]:
tm = TemplateMatching(0.03)

In [10]:
eval_model.get_results_for_all_image_pairs(test_data, tm)

In [11]:
y_true, y_pred = eval_model.generate_output_lists(test_data)

In [12]:
from sklearn.metrics import accuracy_score, balanced_accuracy_score, precision_score, recall_score, f1_score

In [13]:
print(precision_score(y_true, y_pred, average=None))

[0.00371802 1.         0.24886191]


In [14]:
recall_score(y_true, y_pred, average=None)

array([0.99697885, 0.45618724, 1.        ])

In [15]:
f1_score(y_true, y_pred, average=None)
# SAME, DIFFERENT, NONE

array([0.00740841, 0.62655025, 0.39854192])

In [16]:
from mse import MSEComparator

In [17]:
mse_c = MSEComparator(0.9)

In [18]:
eval_model = Evaluation()
list_A, list_B = eval_model.prepare_test_Data("/home/adity/Desktop/projects/image_search/datasets/Test Data/match.csv")
test_data = eval_model.prepare_test_data_Structure(list_A, list_B)
print(test_data[1].clientA, test_data[1].clientB, test_data[1].expected_y, test_data[1].predicted_y)
print(len(test_data))

Processed lines {496}
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Juicy Green Apple Shampoo  350ml'].jpg YType.DIFFERENT YType.NONE
164009


In [19]:
eval_model.get_results_for_all_image_pairs(test_data, mse_c)
y_true, y_pred = eval_model.generate_output_lists(test_data)

In [20]:
recall_score(y_true, y_pred, average=None)
# tp / (tp + fn)

array([0.918429  , 0.99675869, 1.        ])

In [21]:
precision_score(y_true, y_pred, average=None)
# tp / (tp + fp)

array([0.89411765, 0.9998405 , 0.24886191])

In [22]:
f1_score(y_true, y_pred, average=None)
# SAME, DIFFERENT, NONE

array([0.90611028, 0.99829722, 0.39854192])

In [4]:
from ssim import SSIMComparator
ssim_c = SSIMComparator(0.7)

In [ ]:
eval_model = Evaluation()
list_A, list_B = eval_model.prepare_test_Data("/home/adity/Desktop/projects/image_search/datasets/Test Data/match.csv")
test_data = eval_model.prepare_test_data_Structure(list_A, list_B)
print(test_data[1].clientA, test_data[1].clientB, test_data[1].expected_y, test_data[1].predicted_y)
print(len(test_data))
eval_model.get_results_for_all_image_pairs_color(test_data, ssim_c)
y_true, y_pred = eval_model.generate_output_lists(test_data)

Processed lines {496}
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Juicy Green Apple Shampoo  350ml'].jpg YType.DIFFERENT YType.NONE
164009
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Juicy Green Apple Shampoo  350ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03401327133178711
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Coconut & Lychee Conditioner  350ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.030429601669311523
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Coconut & Lychee Nourishing Shampoo 350ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.02995920181274414
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Energize Conditioner 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03171181678771973
['akin fragrance free conditioner 500'].jpg ['Alberto Balsam Energize Sham

['akin fragrance free conditioner 500'].jpg ['Colourless Max Condition Hair Colour Remover 341g'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.06515741348266602
['akin fragrance free conditioner 500'].jpg ['Daniel Galvin Jr Organic Head Volumising Conditioner 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.04925894737243652
['akin fragrance free conditioner 500'].jpg ['Dead Sea Spa Magik Mud Scalp Conditioner 150ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.0436553955078125
['akin fragrance free conditioner 500'].jpg ['Dove Colour Care Conditioner       200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.05714917182922363
['akin fragrance free conditioner 500'].jpg ['Dove Colour Care Shampoo  250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.04535269737243652
['akin fragrance free conditioner 500'].jpg ['Dove Colour Care Shampoo 4

['akin fragrance free conditioner 500'].jpg ['Garnier Ultimate Blends Oat Milk Sensitive Scalp Conditioner 360ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.028485774993896484
['akin fragrance free conditioner 500'].jpg ['Garnier Ultimate Blends Oat Milk Sensitive Scalp Shampoo 360ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03924918174743652
['akin fragrance free conditioner 500'].jpg ['Garnier Ultimate Blends Olive Oil Dry Hair Conditioner 360ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.024443387985229492
['akin fragrance free conditioner 500'].jpg ['Garnier Ultimate Blends Olive Oil Dry Hair Shampoo 360ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.02337479591369629
['akin fragrance free conditioner 500'].jpg ['Garnier Ultimate Blends Repairing Hair Food Papaya Conditioner Damaged Hair 350ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.

['akin fragrance free conditioner 500'].jpg ['Head & Shoulders Citrus Fresh Anti-Dandruff Shampoo 500ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03195357322692871
['akin fragrance free conditioner 500'].jpg ['Head and Shoulders Citrus Fresh Anti Dandruff Shampoo Oily Scalp  250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03679919242858887
['akin fragrance free conditioner 500'].jpg ['Head and Shoulders Citrus Fresh Anti Dandruff Shampoo Oily Scalp  250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.024013042449951172
['akin fragrance free conditioner 500'].jpg ['Head & Shoulders Citrus Fresh Anti-Dandruff Shampoo 500ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.024867534637451172
['akin fragrance free conditioner 500'].jpg ['Head and Shoulders Classic Anti Dandruff Hair Conditioner 275ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YT

['akin fragrance free conditioner 500'].jpg ['Herbal Essences Bio Renew Sulfate Free Hair Conditioner, Aloe and Hemp 275ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03786635398864746
['akin fragrance free conditioner 500'].jpg ['Herbal Essences Bio Renew Sulfate Free Hair Conditioner, Aloe and  Mango 275ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.029739856719970703
['akin fragrance free conditioner 500'].jpg ['Herbal Essences Bio Renew Sulfate Free Shampoo With Potent Aloe and Hemp 380ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.026662349700927734
['akin fragrance free conditioner 500'].jpg ['Herbal Essences Bio Renew Sulfate Free Shampoo With Potent Aloe + Mango 380ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.029190778732299805
['akin fragrance free conditioner 500'].jpg ['Herbal Essences Bio Renew White Grapefruit & Mint Conditioner 200Ml 200m

...

['batiste dry shampoo tropical 400'].jpg ['Tresemme Cleanse + Replenish Shampoo 800ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03697514533996582
['batiste dry shampoo tropical 400'].jpg ['Tresemme Colour Conditioner  400ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03338003158569336
['batiste dry shampoo tropical 400'].jpg ['Tresemme Colour Revitalise Conditioner 800ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03945350646972656
['batiste dry shampoo tropical 400'].jpg ['Tresemme Colour Revitalise Shampoo 800ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03615856170654297
['batiste dry shampoo tropical 400'].jpg ['Tresemme Colour Shampoo  400ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03223466873168945
['batiste dry shampoo tropical 400'].jpg ['Tresemme Deep Cleansing Shampoo 800ml'].jpg , Expected Y:YType

['batiste heavenly volume dry shampoo 200'].jpg ['Aussie Aussome Hair Conditioner Treatment Volumizing Treatment 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03215432167053223
['batiste heavenly volume dry shampoo 200'].jpg ['Aussie Aussome Volume Hair Conditioner For Fine Flat Hair 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.02393198013305664
['batiste heavenly volume dry shampoo 200'].jpg ['Aussie Aussome Volume Shampoo For Fine, Flat Hair  300ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.028947830200195312
['batiste heavenly volume dry shampoo 200'].jpg ['Aussie Calm The Frizz with Australian Hemp Seed Hair Conditioner 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.034032583236694336
['batiste heavenly volume dry shampoo 200'].jpg ['Aussie Calm The Frizz with Australian Hemp Seed Shampoo 300ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YTy

['batiste heavenly volume dry shampoo 200'].jpg ['Dove Pro Age Conditioner 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.03179526329040527
['batiste heavenly volume dry shampoo 200'].jpg ['Dove Pro Age Shampoo 250ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.023819446563720703
['batiste heavenly volume dry shampoo 200'].jpg ['Dove Silver Care Conditioner  200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.02490544319152832
['batiste heavenly volume dry shampoo 200'].jpg ['Dove Silver Care Shampoo 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.030164241790771484
['batiste heavenly volume dry shampoo 200'].jpg ['Elvive Nutri Gloss Luminiser Conditioner 400ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.02362966537475586
['batiste heavenly volume dry shampoo 200'].jpg ['Elvive Nutri Gloss Luminiser Shampoo  400ml'].

['batiste heavenly volume dry shampoo 200'].jpg ['Green People Organic Conditioner Daily Aloe , Vegan 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.030347585678100586
['batiste heavenly volume dry shampoo 200'].jpg ['Green People Organic Conditioner, Moisturising, Vegan 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.02955460548400879
['batiste heavenly volume dry shampoo 200'].jpg ['Green People Organic Conditioner Quinoa & Artichoke, Vegan 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.030717849731445312
['batiste heavenly volume dry shampoo 200'].jpg ['Green People Organic  Irritated Scalp Conditioner, Vegan 200ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.03390145301818848
['batiste heavenly volume dry shampoo 200'].jpg ['Green People Organic Travel Size Shampoo Quinoa & Artichoke, Vegan 100ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.S

['batiste heavenly volume dry shampoo 200'].jpg ['Head and Shoulders Itchy Scalp Eucalyptus Anti Dandruff Shampoo 500ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.029783010482788086
['batiste heavenly volume dry shampoo 200'].jpg ['Head and Shoulders Itchy Scalp Eucalyptus Anti Dandruff Shampoo 500ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.SAME time taken: 0.023817777633666992
['batiste heavenly volume dry shampoo 200'].jpg ['Head and Shoulders Men Ultra Deep Cleansing Anti Dandruff Shampoo 225ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.02909111976623535
['batiste heavenly volume dry shampoo 200'].jpg ['Head and Shoulders Men Ultra Hair Booster Anti Dandruff Shampoo 225ml'].jpg , Expected Y:YType.DIFFERENT , Predicted y: YType.DIFFERENT time taken: 0.025266170501708984
['batiste heavenly volume dry shampoo 200'].jpg ['Head and Shoulders Shampoo Scalp Relief Clinically Proven 130ml'].jpg , Expected Y:

In [ ]:
recall_score(y_true, y_pred, average=None)
# tp / (tp + fn)

In [ ]:
precision_score(y_true, y_pred, average=None)
# tp / (tp + fp)

In [ ]:
f1_score(y_true, y_pred, average=None)
# SAME, DIFFERENT, NONE

In [ ]:
from vgg16 import FeatureExtractor
vgg = FeatureExtractor(1)

In [ ]:
eval_model = Evaluation()
list_A, list_B = eval_model.prepare_test_Data("/home/adity/Desktop/projects/image_search/datasets/Test Data/match.csv")
test_data = eval_model.prepare_test_data_Structure(list_A, list_B)
print(test_data[1].clientA, test_data[1].clientB, test_data[1].expected_y, test_data[1].predicted_y)
print(len(test_data))
eval_model.get_results_for_all_image_pairs(test_data, mse_c)
y_true, y_pred = eval_model.generate_output_lists(test_data)